In [1]:
from __future__ import annotations

import collections
import datetime as dt
import itertools
import random
import pickle

import numpy as np
import pandas as pd

from symbolic_transfer_entropy import symbolic_transfer_entropy

In [2]:
import pickle

In [3]:
import plotly.express as px 
import plotly

plotly.io.templates.defualt='plotly_white'

import plotly.graph_objects as go
from plotly.colors import n_colors
import numpy as np

In [4]:
import textwrap

In [5]:
with open('/data_users1/crazybrokeasian/projects/trans-fer-entropy/topic_labels_20_finalized.pkl','rb') as f:
    topic_labels_dict_raw=pickle.load(f)

topic_labels_dict={k:v.replace('\n','<br>'
)for k,v in topic_labels_dict_raw.items()}

topic_labels_dict_raw={k:v.replace(' \n',''
)for k,v in topic_labels_dict_raw.items()}
topic_labels_dict_raw

topic_labels_dict_50 = {i: textwrap.fill(topic_labels_dict_raw[i], 50).replace("\n", "<br>") for i in topic_labels_dict_raw}
topic_labels_dict_50


topic_labels_dict_str={str(k):v for k,v in topic_labels_dict.items()}

In [6]:
pd.Series(topic_labels_dict_raw.values()).values


array(['Qender-affirming medical care for transgender kids',
       'Pride month corporate marketing backlash and company response',
       'Transgender Montana house representative Zooey Zephyr',
       'Local law enforcement and transgender suspects or victims',
       'Bans on abortion and gender-affirming care',
       'Sexual health & preventative healthcare for women and LGBTQ+ people',
       'Random reporting and q&a blogs including some reporting on transgender people',
       'Republican party electoral politics',
       'Culture wars in education including critical theory and transgender awareness',
       'LGBTQ+ pride month events coverage',
       'Electoral politics and divisions on transgender rights',
       'Guides to local events including LGBTQ+ specific events or media',
       'Transgender women and athletes in sports', 'Movie guides',
       'Online harms to transgender & queer individuals',
       'Dylan Mulvaney Bud Light backlash coverage',
       'Housing mar

In [7]:
pd.read_csv('/home/pranavgoel/trans-fer-entropy/topic_modeling/prior_data_apr_jun_2023/all_texts_combined.csv').query('media_name == "Fox News"')['publish_date'].min()

'2023-05-09 16:05:13'

In [8]:
plots_path='/data_users1/crazybrokeasian/projects/trans-fer-entropy/plots_and_images/topic_modeling'

In [9]:
collection_color_map={'nyt': '#2E498A', 'newyork': '#4B2D6B', 'illinois': '#72C29F', 'california':'#64CDF0', 'fox': '#7E1939', 'texas': '#F5CF65', 'ohio': '#EF9173','florida': '#D68537'}

In [10]:
def load_and_process_topics(url_to_ts, url_to_topic_scores, n_topics=10):
    """
    Given a dict (pkl) and a mapping from url to topic scores, produce a pandas dataframe w/ columns [ts, topic1_count, topic2_count,...]

    Inputs:
        url_to_ts: dict of {url: publication ts}
        url_to_topic_scores: dict of {url: [topic1_score, topic2_score, ...]
        n_topics: number of topics; default 10

    Outputs:
        df_ts_topic: pandas dataframe w/ columns [ts, topic1_count, topic2_count,...]
    """
    ts_to_topics = {}
    for url, ts in url_to_ts.items():
        kw_scores = url_to_topic_scores[url]
        ts_round = pd.to_datetime(ts).floor('D')
        if ts_round in ts_to_topics:
            for idx, sc in enumerate(kw_scores):
                ts_to_topics[ts_round][idx] += sc
        else:
            ts_to_topics[ts_round] = {}
            for idx, sc in enumerate(kw_scores):
                ts_to_topics[ts_round][idx] = sc

    def update_ts_kw_dict(my_ts):
        """
        Given a timestamp, make a dict that contains all the keyword counts for all valid keywords

        Input: my_ts: pandas timestamp

        Output: d {keyword: count}
        """
        d = {'ts': my_ts}
        ts_topic_dict = ts_to_topics.get(my_ts, {})
        for kw in range(n_topics):
            d[topic] = ts_topics_dict.get(topic, 0)
        return d

    ts_topic_dicts = []
    for ts in list(pd.date_range(start='2023-04-01', end='2023-06-30', freq='D')):
        vals = ts_to_topics.get(ts, {})
        d = {'ts': ts}
        for i in range(n_topics):
            d[i] = vals.get(i, 0)
        ts_topic_dicts.append(d)

    return pd.DataFrame(ts_topic_dicts)


def get_media_outlet(media_group, url):
    if media_group in STATES:
        return media_group
    else:
        if 'nytimes.com' in url:
            return 'nytimes.com'
        elif 'foxnews.com' in url:
            return 'foxnews.com'
        else:
            return None



In [11]:
te_results = {i: {} for i in range(20)}
STATES = set(['newyork', 'florida', 'california', 'ohio', 'illinois', 'texas'])
N_TOPICS = 20
combined_df = pd.read_csv('/home/pranavgoel/trans-fer-entropy/topic_modeling/apr_jun_2023_post_irrelevant_article_filtering/all_texts_combined_post_irrelevant_article_filtering.csv') 
print([c for c in combined_df.columns])

print(combined_df['media_group'].unique())

combined_df['publication'] = combined_df.apply(lambda b: get_media_outlet(b.media_group, b.url), axis=1)
combined_df['media_group']=np.where(combined_df['media_name']=='New York Times','nyt',combined_df['media_group'])
combined_df['media_group']=np.where(combined_df['media_name']=='Fox News','fox',combined_df['media_group'])

['Unnamed: 0', 'media_name', 'publish_date', 'title', 'url', 'subtitle', 'text', 'sent_count', 'domain', 'gender_label', 'media_group']
['ohio' 'nytimes_foxnews' 'florida' 'texas' 'illinois' 'newyork'
 'california']


In [12]:
url_to_topic_scores = pickle.load(open('/home/pranavgoel/trans-fer-entropy/topic_modeling/apr_jun_2023_post_irrelevant_article_filtering/url_to_topic_distribution_for_num_topics_{}.pkl'.format(str(20)), 'rb'))

In [13]:
url_topic_df=pd.DataFrame(url_to_topic_scores).T.reset_index()
url_topic_df.head()

combined_df

Unnamed: 0                 media_name                publish_date  \
0            2.0               limaohio.com         2023-04-01 15:46:07   
1            3.0              cleveland.com         2023-04-01 18:34:16   
2            4.0                   wkbn.com         2023-04-01 18:01:43   
3            5.0       lovelandmagazine.com         2023-04-01 11:04:53   
4            6.0              cleveland.com         2023-04-02 05:00:02   
...          ...                        ...                         ...   
9640      7558.0    San Diego Union Tribune  2023-06-30 00:28:44.000000   
9641      7560.0  http://www.hoffmania.com/  2023-06-30 14:02:00.000000   
9642      7561.0                   knzr.com  2023-06-30 18:02:47.000000   
9643      7562.0            Perris Progress  2023-06-30 12:34:48.000000   
9644      7566.0                Tablehopper  2023-06-29 13:51:26.000000   

                                                  title  \
0     Elida schools tackling transgender bathroom de...   
1     Only one protestor shows up for drag story hou...   
2     Illinois café rescued from closure after haras...   
3     Ohio Right to Life makes spurious, anti-trans ...   
4     Ask Amy: My conservative religious views are p...   
...                                                 ...   
9640  Trump and DeSantis court Moms for Liberty in a...   
9641  35 LGBTQ+ owned brands to support this year an...   
9642         Trans Influincer Lashes Out At Beer Brewer   
9643                               FRIDAY June 30, 2023   
9644        This week’s tablehopper: on a cloud. (free)   

                                                    url  \
0     https://www.limaohio.com/top-stories/2023/04/0...   
1     https://www.cleveland.com/news/2023/04/only-on...   
2     https://www.wkbn.com/news/national-world/illin...   
3     https://www.lovelandmagazine.com/ohio-right-to...   
4     https://www.cleveland.com/entertainment/2023/0...   
...                                                 ...   
9640  https://www.sandiegouniontribune.com/news/nati...   
9641  https://www.nbcnews.com/select/shopping/lgbtq-...   
9642  https://www.knzr.com/trans-influincer-lashes-o...   
9643  https://zapinin.com/this-date-in-history/frida...   
9644  https://www.tablehopper.com/newsletter/this-we...   

                                               subtitle  \
0                                                   NaN   
1                                                   NaN   
2     A suburban bakery that had planned to close it...   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
9640  The two leading contenders for the Republican ...   
9641  We spoke to LGBTQ+ business owners about their...   
9642                                                NaN   
9643  Today in History - FRIDAY June 30, 2023 - Toda...   
9644  Read my preview visits to Kuma on Valencia 🍣, ...   

                                                   text  sent_count  \
0     ELIDA — Although parents and educators alike b...          32   
1     CHESTERLAND, Ohio – The much-anticipated prote...          40   
2     LAKE IN THE HILLS, Ill. (WGN-TV) — A suburban ...          23   
3     Right to Life officials claim a reproductive r...          40   
4     Dear Amy: I am a 60-year-old conservative Cath...          50   
...                                                 ...         ...   
9640  Former President Donald Trump poses for a phot...          49   
9641  Pride Month serves as a reminder of the progre...          76   
9642  Transgender influincer Dylan Mulvaney is addre...           9   
9643  Today in History – FRIDAY June 30, 2023\n\nTod...          25   
9644  what’s cookin’\n\nTrans March 2023 at Dolores ...         218   

                        domain  gender_label media_group publication  
0                 limaohio.com             1        oh

In [14]:
topic_master=pd.merge(combined_df, url_topic_df,  left_on='url', right_on='index')
topic_master['publish_date']= pd.to_datetime(topic_master['publish_date'], format='mixed')

topic_master['media_group'].unique()


array(['ohio', 'texas', 'california', 'nyt', 'fox', 'florida', 'newyork',
       'illinois'], dtype=object)

# Temporal Trend

In [15]:
topic_master[list(range(0,20))].sum(axis=1)

0       1.0
1       1.0
2       1.0
3       1.0
4       1.0
       ... 
9640    1.0
9641    1.0
9642    1.0
9643    1.0
9644    1.0
Length: 9645, dtype: float64

In [16]:
daily_trend_topic=topic_master.groupby(pd.Grouper(key='publish_date', freq='D'),)[list(range(0,20))].mean()
# daily_trend_topic.rename(columns=topic_labels_dict, inplace=True)

In [17]:
daily_trend_topic_long=daily_trend_topic.stack().reset_index()
daily_trend_topic_long.columns=['date','topic','mean_prob']


In [53]:
px.line(daily_trend_topic_long, x='date', y='mean_prob', color='topic').update_layout(legend=dict(
    orientation="h",
    # entrywidth=70,
    yanchor="bottom",
    y=1.02,
    xanchor="right",
    x=1
))

In [52]:
temp_area_fig=px.area(daily_trend_topic_long, x='date', y='mean_prob', color='topic', labels={''})

temp_area_fig.update_yaxes(tickformat=".0%")

temp_area_fig.write_image(f'{plots_path}/temporal_area.svg')
temp_area_fig.write_image(f'{plots_path}/temporal_area.png', scale=2)


temp_area_fig



In [51]:
line_graph=px.line(daily_trend_topic_long, x='date', y='mean_prob', color='topic', facet_col='topic', height=900, width=1200,
facet_row_spacing=0.09,
facet_col_wrap=4)

line_graph=line_graph.update_layout(showlegend=False,
).for_each_annotation(lambda a: a.update(text=topic_labels_dict[int(a.text.split("=")[-1])]))

line_graph.update_yaxes(tickformat=".0%")
line_graph.write_image(f'{plots_path}/temporal_line_1.svg')
line_graph.write_image(f'{plots_path}/temporal_line_1.png', scale=2)



line_graph

In [50]:
line_graph_mono=px.line(daily_trend_topic_long, x='date', y='mean_prob', facet_col='topic', height=900, width=1200,
facet_col_wrap=4, facet_row_spacing=0.09,)

line_graph_mono=line_graph_mono.update_layout(showlegend=False,
).for_each_annotation(lambda a: a.update(text=topic_labels_dict[int(a.text.split("=")[-1])]))

line_graph_mono.update_yaxes(tickformat=".0%")
line_graph_mono.write_image(f'{plots_path}/temporal_line_2.svg')
line_graph_mono.write_image(f'{plots_path}/temporal_line_2.png', scale=2)


line_graph_mono

In [49]:
area_temporal_fig=px.area(daily_trend_topic_long, x='date', y='mean_prob', color='topic', facet_col='topic', facet_col_wrap=4,facet_row_spacing=0.09,
height=900, width=1200,).update_layout(showlegend=False,
).for_each_annotation(lambda a: a.update(text=topic_labels_dict[int(a.text.split("=")[-1])]))

area_temporal_fig.update_yaxes(tickformat=".0%")

area_temporal_fig.write_image(f'{plots_path}/temporal_area_1.svg')
area_temporal_fig.write_image(f'{plots_path}/temporal_area_1.png', scale=2)





area_temporal_fig

In [113]:
# px.colors.sequential

In [128]:
temporal_scatter_fig=px.scatter(daily_trend_topic_long.assign(topic=daily_trend_topic_long.topic.map(topic_labels_dict)), 
x='date', y='topic', color='mean_prob', size='mean_prob', height=1100, width=1200,
# color_continuous_scale=px.colors.sequential.Magenta,
# color_continuous_scale=px.colors.diverging.Tropic,

size_max=20,  )


temporal_scatter_fig.write_image(f'{plots_path}/temporal_scatter.svg')
temporal_scatter_fig.write_image(f'{plots_path}/temporal_scatter.png', scale=2)

temporal_scatter_fig

In [129]:
tempoeral_heatmap=px.imshow(daily_trend_topic.rename(columns=topic_labels_dict).T, height=1100,
 )


tempoeral_heatmap.write_image(f'{plots_path}/temporal_heatmap.svg')
tempoeral_heatmap.write_image(f'{plots_path}/temporal_heatmap.png', scale=2)


tempoeral_heatmap

# Temporal per Collection

In [19]:
daily_collection_topic_df=topic_master.groupby([pd.Grouper(key='publish_date', freq='d'),'media_group'])[list(range(0,20))].mean().stack().reset_index(name='mean_prob')

In [20]:
topic_master['media_group'].unique()

array(['ohio', 'texas', 'california', 'nyt', 'fox', 'florida', 'newyork',
       'illinois'], dtype=object)

In [21]:
topic_master.groupby('media_group')['publish_date'].min()

media_group
california   2023-04-01 01:40:05
florida      2023-04-01 18:00:40
fox          2023-05-09 16:05:13
illinois     2023-04-01 13:06:27
newyork      2023-04-01 11:42:42
nyt          2023-04-01 09:00:07
ohio         2023-04-01 11:04:53
texas        2023-04-01 05:01:05
Name: publish_date, dtype: datetime64[ns]

In [22]:
daily_collection_topic_df.rename(columns={'level_2':'topic'}, inplace=True)
daily_collection_topic_df

publish_date media_group  topic  mean_prob
0       2023-04-01  california      0   0.052712
1       2023-04-01  california      1   0.000822
2       2023-04-01  california      2   0.000084
3       2023-04-01  california      3   0.053295
4       2023-04-01  california      4   0.047183
...            ...         ...    ...        ...
12895   2023-06-30       texas     15   0.086760
12896   2023-06-30       texas     16   0.022472
12897   2023-06-30       texas     17   0.298800
12898   2023-06-30       texas     18   0.038048
12899   2023-06-30       texas     19   0.018713

[12900 rows x 4 columns]

In [53]:
# combined_df.query('media_group == "nytimes_foxnews"')['media_name'].value_counts()

In [54]:
# combined_df.query('media_name == "Fox News"')['publish_date'].min()

In [55]:
# combined_df.query('media_name == "Fox News"')['publish_date']

In [47]:
daily_media_topic_fig=px.area(daily_collection_topic_df,
x='publish_date',
y='mean_prob',
color='media_group',
facet_row='topic',
facet_col='media_group',
height=1500,
facet_col_spacing=0.03,
facet_row_spacing=0.01,
color_discrete_map=collection_color_map,
category_orders={"media_group": [ 'nyt', 'newyork','california', 'illinois','fox','florida', 'ohio', 'texas', 
       ]},
width=1100)

daily_media_topic_fig.update_layout(showlegend=False,
# ).for_each_annotation(lambda a: a.update(text=topic_labels_dict_str.get(a.text.split("=")[-1], a.text.split("=")[-1] )))
).for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

daily_media_topic_fig.for_each_xaxis(lambda x: x.update(title=None))
daily_media_topic_fig.for_each_yaxis(lambda y: y.update(title=None))

daily_media_topic_fig.update_yaxes(tickformat=".0%")

daily_media_topic_fig.add_annotation(x=-0.05,y=0.5,
                   text="Topic Distribution", textangle=-90,
                    xref="paper", yref="paper")

daily_media_topic_fig.add_annotation(x=1.05,y=0.5,
                   text="Topic Label", textangle=-270,
                    xref="paper", yref="paper")

# daily_media_topic_fig.add_annotation(x=0.5,y=-0.05,
#                    text="Date", textangle=0,
#                     xref="paper", yref="paper")

# daily_media_topic_fig.update_layout(yaxis2=dict(title="Topic"))

daily_media_topic_fig.write_image(f'{plots_path}/temporal_collection_area.svg')
daily_media_topic_fig.write_image(f'{plots_path}/temporal_collection_area.png', scale=2)


daily_media_topic_fig

In [46]:
daily_media_topic_line_fig=px.line(daily_collection_topic_df,
x='publish_date',
y='mean_prob',
color='media_group',
facet_col='topic',
# facet_col='media_group',
height=1000,
facet_col_spacing=0.03,
facet_row_spacing=0.07,
facet_col_wrap=4,
# alpha=0.4,
color_discrete_map=collection_color_map,
category_orders={"media_group": [ 'nyt', 'newyork','california', 'illinois','fox','florida', 'ohio', 'texas', 
       ]},
width=1100).update_traces(opacity=.8, line=dict( width=1.5))

daily_media_topic_line_fig.update_layout(showlegend=True,
# ).for_each_annotation(lambda a: a.update(text=topic_labels_dict_str.get(a.text.split("=")[-1], a.text.split("=")[-1] )))
).for_each_annotation(lambda a: a.update(text=topic_labels_dict[int(a.text.split("=")[-1])]))

# daily_media_topic_line_fig.for_each_xaxis(lambda x: x.update(title=None))
daily_media_topic_line_fig.for_each_yaxis(lambda y: y.update(title=None))


daily_media_topic_line_fig.update_yaxes(tickformat=".0%")

daily_media_topic_line_fig.add_annotation(x=-0.05,y=0.5,
                   text="Topic Distribution", textangle=-90,
                    xref="paper", yref="paper")


daily_media_topic_line_fig.write_image(f'{plots_path}/temporal_collection_line.svg')
daily_media_topic_line_fig.write_image(f'{plots_path}/temporal_collection_line.png', scale=2)

daily_media_topic_line_fig


# Outlet Distr

In [55]:
media_topic_df=topic_master.groupby(['media_group'])[list(range(0,20))].mean().stack().reset_index(name='mean_prob')
media_topic_df.rename(columns={'level_1':'topic'}, inplace=True)
media_topic_df

media_topic_df['topic_label']=media_topic_df['topic'].map(topic_labels_dict)
media_topic_df

media_group  topic  mean_prob  \
0    california      0   0.069291   
1    california      1   0.021589   
2    california      2   0.028597   
3    california      3   0.050589   
4    california      4   0.067585   
..          ...    ...        ...   
155       texas     15   0.062889   
156       texas     16   0.029977   
157       texas     17   0.037439   
158       texas     18   0.048336   
159       texas     19   0.024701   

                                           topic_label  
0    Qender-affirming medical <br> care for transge...  
1    Pride month corporate marketing <br> backlash ...  
2    Transgender Montana house <br> representative ...  
3    Local law enforcement and <br> transgender sus...  
4      Bans on abortion and <br> gender-affirming care  
..                                                 ...  
155    Dylan Mulvaney Bud <br> Light backlash coverage  
156  Housing market & policy <br> including queer b...  
157  Supreme court rulings <br> around LGBTQ+ discr...  
158  K-12 school policies <br> regarding LGBTQ+ stu...  
159                International LGBTQ+ rights updates  

[160 rows x 4 columns]

In [138]:
collection_hori_bar_fig=px.bar(media_topic_df,
x='mean_prob',
y='media_group',
color='topic_label',
height=700,
width=1200,
text=media_topic_df['mean_prob'].map(lambda x: f"{x:.0%}"),
orientation='h')


collection_hori_bar_fig.write_image(f'{plots_path}/collection_hori_bar.svg')
collection_hori_bar_fig.write_image(f'{plots_path}/collection_hori_bar.png', scale=2)




collection_hori_bar_fig

In [57]:
topic_per_media=px.bar(media_topic_df,
y='mean_prob',
# x='topic_label',
color='media_group',
x='media_group',
height=900,
facet_col_wrap=4,
width=1250,
facet_col_spacing=0.03,
facet_row_spacing=0.08,
text=media_topic_df['mean_prob'].map(lambda x: f"{x:.0%}"),
color_discrete_map=collection_color_map,
category_orders={"media_group": [ 'nyt', 'newyork','california', 'illinois','fox','florida', 'ohio', 'texas', 
       ]},
facet_col='topic_label')

topic_per_media=topic_per_media.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
topic_per_media.update_yaxes(tickformat=".0%")

topic_per_media.for_each_xaxis(lambda x: x.update(title='Media Group'))
topic_per_media.for_each_yaxis(lambda y: y.update(title=None))


topic_per_media.add_annotation(x=-0.05,y=0.5,
                   text="Topic Distribution", textangle=-90,
                    xref="paper", yref="paper")

topic_per_media.write_image(f'{plots_path}/collection_bar_facet.svg')
topic_per_media.write_image(f'{plots_path}/collection_bar_facet.png', scale=2)




topic_per_media

# Media Distr

In [16]:
topic_master.groupby('media_group').size()

media_group
california    3171
florida       1090
fox            546
illinois       547
newyork       2125
nyt            107
ohio           525
texas         1534
dtype: int64

In [18]:
topic_master.groupby('media_group')['media_name'].nunique()

media_group
california    266
florida        65
fox             1
illinois       61
newyork       109
nyt             1
ohio           41
texas          85
Name: media_name, dtype: int64

In [28]:
topic_master[list(range(20))].mean().round(2)

0     0.08
1     0.03
2     0.02
3     0.04
4     0.08
5     0.03
6     0.12
7     0.04
8     0.06
9     0.08
10    0.03
11    0.01
12    0.05
13    0.04
14    0.05
15    0.06
16    0.04
17    0.04
18    0.06
19    0.02
dtype: float64